<small>Note: This notebook is adapted from the [AbLang2](https://github.com/TobiasHeOl/AbLang2) model's GitHub repository. It is used to verify that the Hugging Face implementation functions correctly and produces the same output as the original model.

In [1]:
!rm -rf ~/.cache/huggingface/hub/models--hemantn--ablang2

In [2]:
import sys
import os
import numpy as np
from transformers import AutoModel, AutoTokenizer
from huggingface_hub import hf_hub_download

# **0. Sequence input and its format**

AbLang2 takes as input either the individual heavy variable domain (VH), light variable domain (VL), or the full variable domain (Fv).

Each record (antibody) needs to be a list with the VH as the first element and the VL as the second. If either the VH or VL is not known, leave an empty string.

An asterisk (\*) is used for masking. It is recommended to mask residues which you are interested in mutating.

**NB:** It is important that the VH and VL sequence is ordered correctly.

In [3]:
seq1 = [
    'EVQLLESGGEVKKPGASVKVSCRASGYTFRNYGLTWVRQAPGQGLEWMGWISAYNGNTNYAQKFQGRVTLTTDTSTSTAYMELRSLRSDDTAVYFCARDVPGHGAAFMDVWGTGTTVTVSS', # VH sequence
    'DIQLTQSPLSLPVTLGQPASISCRSSQSLEASDTNIYLSWFQQRPGQSPRRLIYKISNRDSGVPDRFSGSGSGTHFTLRISRVEADDVAVYYCMQGTHWPPAFGQGTKVDIK' # VL sequence
]
seq2 = [
    'EVQLLESGGEVKKPGASVKVSCRASGYTFRNYGLTWVRQAPGQGLEWMGWISAYNGNTNYAQKFQGRVTLTTDTSTSTAYMELRSLRSDDTAVYFCARDVPGHGAAFMDVWGTGTT',
    'PVTLGQPASISCRSSQSLEASDTNIYLSWFQQRPGQSPRRLIYKISNRDSGVPDRFSGSGSGTHFTLRISRVEADDVAVYYCMQGTHWPPAFGQGTKVDIK'
]
seq3 = [
    'EVQLLESGGEVKKPGASVKVSCRASGYTFRNYGLTWVRQAPGQGLEWMGWISAYNGNTNYAQKFQGRVTLTTDTSTSTAYMELRSLRSDDTAVYFCARDVPGHGAAFMDVWGTGTTVTVSS',
    '' # The VL sequence is not known, so an empty string is left instead. 
]
seq4 = [
    '',
    'DIQLTQSPLSLPVTLGQPASISCRSSQSLEASDTNIYLSWFQQRPGQSPRRLIYKISNRDSGVPDRFSGSGSGTHFTLRISRVEADDVAVYYCMQGTHWPPAFGQGTKVDIK'
]
seq5 = [
    'EVQ***SGGEVKKPGASVKVSCRASGYTFRNYGLTWVRQAPGQGLEWMGWISAYNGNTNYAQKFQGRVTLTTDTSTSTAYMELRSLRSDDTAVYFCAR**PGHGAAFMDVWGTGTTVTVSS', # (*) is used to mask certain residues
    'DIQLTQSPLSLPVTLGQPASISCRSS*SLEASDTNIYLSWFQQRPGQSPRRLIYKI*NRDSGVPDRFSGSGSGTHFTLRISRVEADDVAVYYCMQGTHWPPAFGQGTKVDIK'
]

all_seqs = [seq1, seq2, seq3, seq4, seq5]
only_both_chains_seqs = [seq1, seq2, seq5]

# **1. How to use AbLang2**

AbLang2 can be downloaded and used in its raw form as seen below. For convenience, we have also developed different "modes" which can be used for specific use cases (see Section 2) 

In [4]:
# Load model and tokenizer from Hugging Face Hub
model = AutoModel.from_pretrained("hemantn/ablang2", trust_remote_code=True)
tokenizer = AutoTokenizer.from_pretrained("hemantn/ablang2", trust_remote_code=True)

# Find the cached model directory and import adapter
adapter_path = hf_hub_download(repo_id="hemantn/ablang2", filename="adapter.py")
cached_model_dir = os.path.dirname(adapter_path)
sys.path.insert(0, cached_model_dir)

# Import and create the adapter
from adapter import AbLang2PairedHuggingFaceAdapter
ablang = AbLang2PairedHuggingFaceAdapter(model=model, tokenizer=tokenizer)

config.json:   0%|          | 0.00/763 [00:00<?, ?B/s]

configuration_ablang2paired.py: 0.00B [00:00, ?B/s]

A new version of the following files was downloaded from https://huggingface.co/hemantn/ablang2:
- configuration_ablang2paired.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.


modeling_ablang2paired.py: 0.00B [00:00, ?B/s]

A new version of the following files was downloaded from https://huggingface.co/hemantn/ablang2:
- modeling_ablang2paired.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.
/home/hn533621/.conda/envs/lib_transformer/lib/python3.10/site-packages/huggingface_hub/file_download.py:943: FutureWarning: `resume_download` is deprecated and will be removed in version 1.0.0. Downloads always resume when possible. If you want to force a new download, use `force_download=True`.
  warnings.warn(


...

tokenizer_ablang2paired.py: 0.00B [00:00, ?B/s]

A new version of the following files was downloaded from https://huggingface.co/hemantn/ablang2:
- tokenizer_ablang2paired.py
. Make sure to double-check they do not contain any added malicious code. To avoid downloading new versions of the code file, you can pin a revision.


vocab.json:   0%|          | 0.00/331 [00:00<?, ?B/s]

adapter.py: 0.00B [00:00, ?B/s]

📁 Files in current directory (/home/hn533621/.cache/huggingface/hub/models--hemantn--ablang2/snapshots/13d4401549c368256c517dc13b8ed3d8b28d5e87):
   adapter.py
   configuration_ablang2paired.py
   tokenizer_ablang2paired.py
   modeling_ablang2paired.py
✅ Successfully imported utility modules from cache directory


# **2. Different modes for specific usecases**

AbLang2 has already been implemented for a variety of different usecases. The benefit of these modes is that they handle extra tokens such as start, stop and separation tokens.

1. seqcoding: Generates sequence representations for each sequence
2. rescoding: Generates residue representations for each residue in each sequence
3. likelihood: Generates likelihoods for each amino acid at each position in each sequence
4. probability: Generates probabilities for each amino acid at each position in each sequence
5. pseudo_log_likelihood: Returns the pseudo log likelihood for a sequence (based on masking each residue one at a time)
6. confidence: Returns a fast calculation of the log likelihood for a sequence (based on a single pass with no masking)
7. restore: Restores masked residues

### **AbLang2 can also align the resulting representations using ANARCI**

This can be done for 'rescoding', 'likelihood', and 'probability'. This is done by setting the argument "align=True".

**NB**: Align can only be used on input with the same format, i.e. either all heavy, all light, or all both heavy and light.

### **The align argument can also be used to restore variable missing lengths**

For this, use "align=True" with the 'restore' mode.

In [5]:
valid_modes = [
    'seqcoding', 'rescoding', 'likelihood', 'probability',
    'pseudo_log_likelihood', 'confidence', 'restore' 
]

## **seqcoding** 

The seqcodings represents each sequence as a 480 sized embedding. It is derived from averaging across each rescoding embedding for a given sequence, including extra tokens. 

**NB:** Seqcodings can also be derived in other ways like using the sum or averaging across only parts of the input such as the CDRs. For such cases please use and adapt the below rescoding.

In [6]:
ablang(all_seqs, mode='seqcoding')


array([[-0.2520631 ,  0.18189636,  0.00887137, ...,  0.15365516,
        -0.14508602, -0.13381316],
       [-0.24383117,  0.20946886,  0.07412891, ...,  0.15079288,
        -0.13847049, -0.07304662],
       [-0.20084268,  0.23405147, -0.00103735, ...,  0.07450922,
        -0.08084311, -0.21812904],
       [-0.12659703,  0.3051279 , -0.15117611, ..., -0.20749238,
        -0.10453435, -0.0787883 ],
       [-0.2955319 ,  0.17239201,  0.05676926, ...,  0.15943624,
        -0.16615382, -0.15569784]], shape=(5, 480), dtype=float32)

## **rescoding / likelihood / probability**

The rescodings represents each residue as a 480 sized embedding. The likelihoods represents each residue as the predicted logits for each character in the vocabulary. The probabilities represents the normalised likelihoods.

**NB:** The output includes extra tokens (start, stop and separation tokens) in the format "<VH_seq>|<VL_seq>". The length of the output is therefore 5 longer than the VH and VL.

**NB:** By default the representations are derived using a single forward pass. To prevent the predicted likelihood and probability to be affected by the input residue at each position, setting the "stepwise_masking" argument to True can be used. This will run a forward pass for each position with the residue at that position masked. This is much slower than running a single forward pass.

In [7]:
ablang(all_seqs, mode='rescoding', stepwise_masking = False)

[array([[-0.40741208, -0.5118987 ,  0.06096708, ...,  0.3268144 ,
          0.03920235, -0.36715826],
        [-0.5768883 ,  0.38245413, -0.21791998, ...,  0.01250262,
         -0.08844463, -0.32367525],
        [-0.1475935 ,  0.39639047, -0.38226923, ..., -0.10119921,
         -0.41469565, -0.00319315],
        ...,
        [-0.14358369,  0.3124389 , -0.30157998, ..., -0.13289244,
         -0.45353398, -0.07878865],
        [ 0.17538925,  0.24394299,  0.20141171, ...,  0.14587352,
         -0.38479003,  0.07409196],
        [-0.23031706, -0.35487285,  0.1960684 , ..., -0.1283362 ,
          0.31107333, -0.3265108 ]], shape=(238, 480), dtype=float32),
 array([[-0.41981837, -0.3666375 ,  0.10595217, ...,  0.3903574 ,
          0.0382378 , -0.36337993],
        [-0.5054137 ,  0.38347068, -0.10992069, ..., -0.05231472,
         -0.13636623, -0.34830108],
        [-0.06784609,  0.69349885, -0.4212398 , ..., -0.24805346,
         -0.39583805, -0.10972726],
        ...,
        [-0.02212614,

## **Align rescoding/likelihood/probability output**

For the 'rescoding', 'likelihood', and 'probability' modes, the output can also be aligned using the argument "align=True".

This is done using the antibody numbering tool ANARCI, and requires manually installing **Pandas** and **[ANARCI](https://github.com/oxpig/ANARCI)**.

**NB**: Align can only be used on input with the same format, i.e. either all heavy, all light, or all both heavy and light.

In [8]:
results = ablang(only_both_chains_seqs, mode='likelihood', align=True)

print(results.number_alignment)
print(results.aligned_seqs)
print(results.aligned_embeds)

['<' '1 ' '2 ' '3 ' '4 ' '5 ' '6 ' '7 ' '8 ' '9 ' '11 ' '12 ' '13 ' '14 '
 '15 ' '16 ' '17 ' '18 ' '19 ' '20 ' '21 ' '22 ' '23 ' '24 ' '25 ' '26 '
 '27 ' '28 ' '29 ' '30 ' '35 ' '36 ' '37 ' '38 ' '39 ' '40 ' '41 ' '42 '
 '43 ' '44 ' '45 ' '46 ' '47 ' '48 ' '49 ' '50 ' '51 ' '52 ' '53 ' '54 '
 '55 ' '56 ' '57 ' '58 ' '59 ' '62 ' '63 ' '64 ' '65 ' '66 ' '67 ' '68 '
 '69 ' '70 ' '71 ' '72 ' '74 ' '75 ' '76 ' '77 ' '78 ' '79 ' '80 ' '81 '
 '82 ' '83 ' '84 ' '85 ' '86 ' '87 ' '88 ' '89 ' '90 ' '91 ' '92 ' '93 '
 '94 ' '95 ' '96 ' '97 ' '98 ' '99 ' '100 ' '101 ' '102 ' '103 ' '104 '
 '105 ' '106 ' '107 ' '108 ' '109 ' '110 ' '111 ' '112A' '112 ' '113 '
 '114 ' '115 ' '116 ' '117 ' '118 ' '119 ' '120 ' '121 ' '122 ' '123 '
 '124 ' '125 ' '126 ' '127 ' '128 ' '>' '|' '<' '1 ' '2 ' '3 ' '4 ' '5 '
 '6 ' '7 ' '8 ' '9 ' '10 ' '11 ' '12 ' '13 ' '14 ' '15 ' '16 ' '17 ' '18 '
 '19 ' '20 ' '21 ' '22 ' '23 ' '24 ' '25 ' '26 ' '27 ' '28 ' '29 ' '30 '
 '31 ' '32 ' '34 ' '35 ' '36 ' '37 ' '38 ' '39 ' '40 

In [9]:
ablang(only_both_chains_seqs, mode='probability')

[array([[9.9955505e-01, 2.9358694e-06, 2.4716087e-06, ..., 3.5776201e-11,
         9.1196831e-08, 7.0967326e-05],
        [4.1573694e-06, 4.1619489e-07, 2.5800944e-06, ..., 3.4650952e-10,
         1.0159109e-08, 1.6279575e-06],
        [7.8059600e-08, 1.2794037e-03, 4.0645118e-05, ..., 3.0375720e-09,
         1.8879491e-10, 4.2010839e-08],
        ...,
        [3.4210879e-07, 1.7195340e-03, 1.8477240e-05, ..., 1.5137445e-10,
         6.4255873e-10, 8.2064140e-08],
        [9.1038084e-09, 4.5161755e-06, 5.4411950e-05, ..., 9.1139631e-11,
         6.0862085e-08, 8.1761966e-09],
        [8.5759175e-04, 2.0104915e-05, 3.9023766e-06, ..., 4.5562460e-11,
         8.1156479e-08, 5.4990651e-05]], shape=(238, 26), dtype=float32),
 array([[9.9939799e-01, 4.1499175e-06, 1.8611167e-05, ..., 1.8139243e-10,
         5.5649299e-08, 1.2583815e-04],
        [1.6735513e-06, 5.4332406e-07, 3.4143472e-06, ..., 3.1693398e-10,
         7.1501400e-09, 9.6832969e-07],
        [3.7784993e-08, 1.2377645e-04, 1.

## **Pseudo log likelihood and Confidence scores**

The pseudo log likelihood and confidence represents two methods for calculating the uncertainty for the input sequence.

- pseudo_log_likelihood: For each position, the pseudo log likelihood is calculated when predicting the masked residue. The final score is an average across the whole input. This is similar to the approach taken in the ESM-2 paper for calculating pseudo perplexity [(Lin et al., 2023)](https://doi.org/10.1126/science.ade2574).

- confidence: For each position, the log likelihood is calculated without masking the residue. The final score is an average across the whole input. 

**NB:** The **confidence is fast** to compute, requiring only a single forward pass per input. **Pseudo log likelihood is slow** to calculate, requiring L forward passes per input, where L is the length of the input.

**NB:** It is recommended to use **pseudo log likelihood for final results** and **confidence for exploratory work**.

In [10]:
results = ablang(all_seqs, mode='pseudo_log_likelihood')
np.exp(-results) # convert to pseudo perplexity

array([1.96673731, 2.04801253, 2.09881898, 1.82533665, 1.97255249])

In [11]:
results = ablang(all_seqs, mode='confidence')
np.exp(-results)

array([1.2636038, 1.126463 , 1.3123759, 1.2140924, 1.1805094],
      dtype=float32)

## **restore**

This mode can be used to restore masked residues, and fragmented regions with "align=True". 

In [12]:
restored = ablang(only_both_chains_seqs, mode='restore')
restored

array(['<EVQLLESGGEVKKPGASVKVSCRASGYTFRNYGLTWVRQAPGQGLEWMGWISAYNGNTNYAQKFQGRVTLTTDTSTSTAYMELRSLRSDDTAVYFCARDVPGHGAAFMDVWGTGTTVTVSS>|<DIQLTQSPLSLPVTLGQPASISCRSSQSLEASDTNIYLSWFQQRPGQSPRRLIYKISNRDSGVPDRFSGSGSGTHFTLRISRVEADDVAVYYCMQGTHWPPAFGQGTKVDIK>',
       '<EVQLLESGGEVKKPGASVKVSCRASGYTFRNYGLTWVRQAPGQGLEWMGWISAYNGNTNYAQKFQGRVTLTTDTSTSTAYMELRSLRSDDTAVYFCARDVPGHGAAFMDVWGTGTT>|<PVTLGQPASISCRSSQSLEASDTNIYLSWFQQRPGQSPRRLIYKISNRDSGVPDRFSGSGSGTHFTLRISRVEADDVAVYYCMQGTHWPPAFGQGTKVDIK>',
       '<EVQLVQSGGEVKKPGASVKVSCRASGYTFRNYGLTWVRQAPGQGLEWMGWISAYNGNTNYAQKFQGRVTLTTDTSTSTAYMELRSLRSDDTAVYFCARDPPGHGAAFMDVWGTGTTVTVSS>|<DIQLTQSPLSLPVTLGQPASISCRSSQSLEASDTNIYLSWFQQRPGQSPRRLIYKISNRDSGVPDRFSGSGSGTHFTLRISRVEADDVAVYYCMQGTHWPPAFGQGTKVDIK>'],
      dtype='<U238')

In [13]:
restored = ablang(only_both_chains_seqs, mode='restore', align = True)
restored

array(['<EVQLLESGGEVKKPGASVKVSCRASGYTFRNYGLTWVRQAPGQGLEWMGWISAYNGNTNYAQKFQGRVTLTTDTSTSTAYMELRSLRSDDTAVYFCARDVPGHGAAFMDVWGTGTTVTVSS>|<DIQLTQSPLSLPVTLGQPASISCRSSQSLEASDTNIYLSWFQQRPGQSPRRLIYKISNRDSGVPDRFSGSGSGTHFTLRISRVEADDVAVYYCMQGTHWPPAFGQGTKVDIK>',
       '<EVQLLESGGEVKKPGASVKVSCRASGYTFRNYGLTWVRQAPGQGLEWMGWISAYNGNTNYAQKFQGRVTLTTDTSTSTAYMELRSLRSDDTAVYFCARDVPGHGAAFMDVWGTGTTVTVSS>|<DVVMTQSPLSLPVTLGQPASISCRSSQSLEASDTNIYLSWFQQRPGQSPRRLIYKISNRDSGVPDRFSGSGSGTHFTLRISRVEADDVAVYYCMQGTHWPPAFGQGTKVDIK>',
       '<QVQLVQSGGEVKKPGASVKVSCRASGYTFRNYGLTWVRQAPGQGLEWMGWISAYNGNTNYAQKFQGRVTLTTDTSTSTAYMELRSLRSDDTAVYFCARDPPGHGAAFMDVWGTGTTVTVSS>|<DIQLTQSPLSLPVTLGQPASISCRSSQSLEASDTNIYLSWFQQRPGQSPRRLIYKISNRDSGVPDRFSGSGSGTHFTLRISRVEADDVAVYYCMQGTHWPPAFGQGTKVDIK>'],
      dtype='<U238')